 # Opis notatnika

 Ten notatnik inicjuje naszą pracę nad warsztatem końcowym. Naszym zadaniem tutaj jest pobranie udostępnionych nam danych do obszaru roboczego, które w następnym kroku wgramy na naszą bazę danych. Ich obróbka oraz analiza zostanie przeprowadzona w specjalnie do tego celu przygotowanych kolejnych notatnikach.

 Na potrzeby tego warsztatu został stworzony dedykowany serwis API, który dostępny jest pod adresem: https://api-datalab.coderslab.com/api/v2. Dodatkowo udostępniona została dokumentacja, z którą można zapoznać się tutaj: [klik](https://api-datalab.coderslab.com/v2/docs/).

 > Dokumentacja jest czysto techniczna i ma na celu prezentację dostępnych endpointów wraz ze zwracanym typem. W celu przetestowania należy kliknąć przysisk `Authorize`, podać token (dostępny poniżej), a następnie `Try it out!` oraz uzupełnić wymagane pola (parametry requesta).

 Zgodnie z dokumentacją stwierdzamy, że udostępnione zostały nam 4 endpointy:
 - `airport` - dane o lotnisku,
 - `weather` - informacje o zarejestrowaniej pogodzie na lotnisku danego dnia,
 - `aircraft` - dane o samolotach
 - `flights` - dane o wylotach z danego lotniska per dzień.

 Wszystkie te źródła musimy pobrać, aby być w stanie wykonać całość warsztatu. W celu pobrania informacji, gdzie wymagany jest paramatr `airportId`, posłużymy się listą z pliku `airports.csv`.

 Przy wykonywaniu tego zadania możesz posłużyć się tym tokenem: `iKRsQ8vdqgT903o2vH1rsejOeQ0F7YC9TvutH6Wk`.

 ### Uwagi
 - Ze względów ćwiczeniowych, konstrukcja poszczególnych endpointów jest różna – w trakcie pracy dokładnie przyjrzyj się, w jaki sposób należy wykonać zapytanie, aby otrzymać odpowiedź.
 - Pamiętaj o dodaniu `sleep` pomiędzy poszczególnymi wywołaniami endpoint.
 - Limit wywołań API to 1000/min, zadbaj o nieprzekroczenie tego limitu – w przeciwnym wypadku będzie zwracany błąd 429.

 # Konfiguracja notatnika

 Tutaj zaimportuj wymagane biblioteki

In [13]:
import json
import requests
import csv
import pandas as pd
import time
import datetime
from datetime import datetime
from dateutil.relativedelta import relativedelta

 Tutaj zdefiniuj paramatry połączenia do API

In [14]:
authorization = "iKRsQ8vdqgT903o2vH1rsejOeQ0F7YC9TvutH6Wk"
API = 'https://api-datalab.coderslab.com/api/v2'

 Tutaj wczytaj plik `airports.csv` i dostosuj do dalszych kroków w celu pobierania z kolejnych endpointów. Lista lotnisk jest dostępna w kolumnie `origin_airport_id`.

In [15]:
airport_id_initial = []

with open(r'/content/airports.csv', newline='') as my_file:
    airports = csv.reader(my_file)
    for i in airports:
        airport_id_initial.append(i)
    print(airport_id_initial)


[['origin_airport_id'], ['10874'], ['11233'], ['13360'], ['15008'], ['11638'], ['14150'], ['15323'], ['14814'], ['12007'], ['11337'], ['13342'], ['15070'], ['13244'], ['12280'], ['15096'], ['11641'], ['13832'], ['10268'], ['10397'], ['15041'], ['10529'], ['12119'], ['11537'], ['11092'], ['10581'], ['13829'], ['15389'], ['10140'], ['12389'], ['11648'], ['15023'], ['11982'], ['10967'], ['11525'], ['10792'], ['14259'], ['11637'], ['10466'], ['10599'], ['10208'], ['15841'], ['14831'], ['12898'], ['13241'], ['13367'], ['11481'], ['14108'], ['13931'], ['13873'], ['10157'], ['10245'], ['11146'], ['13277'], ['11292'], ['11109'], ['13459'], ['11775'], ['16218'], ['14698'], ['14252'], ['13256'], ['13139'], ['12250'], ['11259'], ['11468'], ['14952'], ['12402'], ['14574'], ['11996'], ['11977'], ['11867'], ['11203'], ['11995'], ['15016'], ['10747'], ['14905'], ['12012'], ['14783'], ['14730'], ['10431'], ['10434'], ['16869'], ['10408'], ['12264'], ['11618'], ['15304'], ['13577'], ['12954'], ['11624'

In [16]:
airportId = [int(e[0]) for e in airport_id_initial[1:]]
airportId

[10874,
 11233,
 13360,
 15008,
 11638,
 14150,
 15323,
 14814,
 12007,
 11337,
 13342,
 15070,
 13244,
 12280,
 15096,
 11641,
 13832,
 10268,
 10397,
 15041,
 10529,
 12119,
 11537,
 11092,
 10581,
 13829,
 15389,
 10140,
 12389,
 11648,
 15023,
 11982,
 10967,
 11525,
 10792,
 14259,
 11637,
 10466,
 10599,
 10208,
 15841,
 14831,
 12898,
 13241,
 13367,
 11481,
 14108,
 13931,
 13873,
 10157,
 10245,
 11146,
 13277,
 11292,
 11109,
 13459,
 11775,
 16218,
 14698,
 14252,
 13256,
 13139,
 12250,
 11259,
 11468,
 14952,
 12402,
 14574,
 11996,
 11977,
 11867,
 11203,
 11995,
 15016,
 10747,
 14905,
 12012,
 14783,
 14730,
 10431,
 10434,
 16869,
 10408,
 12264,
 11618,
 15304,
 13577,
 12954,
 11624,
 13541,
 13422,
 14057,
 13232,
 10800,
 14689,
 12391,
 10868,
 14711,
 10257,
 11067,
 10562,
 11695,
 13796,
 14109,
 13970,
 14193,
 11076,
 14092,
 11122,
 11288,
 11308,
 10754,
 12884,
 15376,
 14588,
 11884,
 12915,
 13851,
 14843,
 11603,
 14457,
 12206,
 11252,
 11905,
 15412,


 # Pobieranie `Airport`
 Zapoznaj się z dokumentacją endpointu `airport`, a następnie pobierz dane dot. poszczególnych lotnisk. Wyniki tego kroku zapisz do ramki `airport_df`, a następnie zapisz do pliku `csv`.

 ### Wskazówki
 - Nie wszystkie lotniska dostępne w pliku `airports.csv`, są dostępne w endpoint. Zadbaj o odpowiednie obsłużenie takiej sytuacji,
 - Do skonwertowania wyników przydatna może okazać się metoda `Pandas` - [from_records](https://pandas.pydata.org/docs/reference/api/pandas.DataFrame.from_records.html),
 - Artykuł LMS: `Python - analiza danych > Dzień 4 - API > Uwierzytelnianie`
 - Artykuł LMS: `Python - analiza danych > Przygotowanie do zjazdu 2`

 Tutaj pobierz dane z endpoint'u `airport`

In [ ]:
airports = []

for i in airportId:
    time.sleep(2)
    response = requests.get(f'https://api-datalab.coderslab.com/api/v2/airport/{i}', headers={'Authorization': f'{authorization}'})
    if response.status_code == 200:
        airports.append(response.json())
    else:
        pass

In [ ]:
airports

[{'ORIGIN_AIRPORT_ID': 11638,
  'DISPLAY_AIRPORT_NAME': 'Fresno Air Terminal',
  'ORIGIN_CITY_NAME': 'Fresno, CA',
  'NAME': 'FRESNO YOSEMITE INTERNATIONAL, CA US'},
 {'ORIGIN_AIRPORT_ID': 13342,
  'DISPLAY_AIRPORT_NAME': 'General Mitchell Field',
  'ORIGIN_CITY_NAME': 'Milwaukee, WI',
  'NAME': 'MILWAUKEE MITCHELL AIRPORT, WI US'},
 {'ORIGIN_AIRPORT_ID': 13244,
  'DISPLAY_AIRPORT_NAME': 'Memphis International',
  'ORIGIN_CITY_NAME': 'Memphis, TN',
  'NAME': 'MEMPHIS INTERNATIONAL AIRPORT, TN US'},
 {'ORIGIN_AIRPORT_ID': 15096,
  'DISPLAY_AIRPORT_NAME': 'Syracuse Hancock International',
  'ORIGIN_CITY_NAME': 'Syracuse, NY',
  'NAME': 'SYRACUSE HANCOCK INTERNATIONAL AIRPORT, NY US'},
 {'ORIGIN_AIRPORT_ID': 10397,
  'DISPLAY_AIRPORT_NAME': 'Atlanta Municipal',
  'ORIGIN_CITY_NAME': 'Atlanta, GA',
  'NAME': 'ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US'},
 {'ORIGIN_AIRPORT_ID': 10529,
  'DISPLAY_AIRPORT_NAME': 'Bradley International',
  'ORIGIN_CITY_NAME': 'Hartford, CT',
  'NA

In [ ]:
airport_df = pd.DataFrame.from_records(airports)
airport_df

ORIGIN_AIRPORT_ID              DISPLAY_AIRPORT_NAME  ORIGIN_CITY_NAME  \
0               11638               Fresno Air Terminal        Fresno, CA   
1               13342            General Mitchell Field     Milwaukee, WI   
2               13244             Memphis International       Memphis, TN   
3               15096    Syracuse Hancock International      Syracuse, NY   
4               10397                 Atlanta Municipal       Atlanta, GA   
..                ...                               ...               ...   
92              13198         Kansas City International   Kansas City, MO   
93              10423  Austin - Bergstrom International        Austin, TX   
94              15370               Tulsa International         Tulsa, OK   
95              13303               Miami International         Miami, FL   
96              10693        Myrtle Beach International  Myrtle Beach, SC   

                                                 NAME  
0                FRESNO YOSEMITE INTERNATIONAL, CA US  
1                   MILWAUKEE MITCHELL AIRPORT, WI US  
2                MEMPHIS INTERNATIONAL AIRPORT, TN US  
3       SYRACUSE HANCOCK INTERNATIONAL AIRPORT, NY US  
4   ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPO...  
..                                                ...  
92           KANSAS CITY INTERNATIONAL AIRPORT, MO US  
93      AUSTIN BERGSTROM INTERNATIONAL AIRPORT, TX US  
94     OKLAHOMA CITY WILL ROGERS WORLD AIRPORT, OK US  
95                 MIAMI INTERNATIONAL AIRPORT, FL US  
96                          NORTH MYRTLE BEACH, SC US  

[97 rows x 4 columns]

 ## Sprawdzenie
 Uruchom kod poniżej, aby sprawdzić czy ta część została poprawnie wykonana

In [ ]:
airport_df_expected_shape = (97, 4)
assert airport_df_expected_shape == airport_df.shape

 Tutaj zapisz ramkę `airport_df` do pliku `airport_list.csv`

In [ ]:
airport_df.to_csv(r'C:\Users\urszu\OneDrive\Pulpit\CodersLab - cwiczenia\Projekt koncowy\data\raw\airport_list.csv', index=False)

 # Pobieranie `Weather`
 Zapoznaj się z dokumentacją endpotu `Weather`, następnie pobierz dane dotyczące zarejestrowanej pogody na poszczególnych lotniskach. Wyniki zapisz do ramki `weather_df`, a później do pliku `airport_weather.csv`.

 Wskazówki:
 - Ze względu na wolumen danych, które tutaj się pobiorą, odradzamy zapisywanie danych bezpośrednio do ramki. Rekomendujemy podejście podobne do tego z warsztatu na kursie `Python - analiza danych` - `Dzień 10 - Warsztat > Warsztat > Scrapowanie danych`, czyli stworzenie listy, a następnie przekonwertowanie jej w postać ramki.
 - Data początkowa danych to `2019-01-01`, zaś data końcowa to `2020-03-31`, czyli 15 miesięcy,
 - Ze względu na czas, jaki ten krok będzie się wykonywał, warto dodać w pętli instrukcję (lub kilka) `print`, aby monitorować przebieg wykonywania tego kroku.
 - Przy dodawaniu miesięcy do daty może przydać się metoda [relativedelta](https://www.geeksforgeeks.org/python-get-month-from-year-and-weekday/).

In [17]:
start_date = '2019-01-01'
end_date = '2020-03-31'

start_date = datetime.strptime(start_date, '%Y-%m-%d')
end_date = datetime.strptime(end_date, '%Y-%m-%d')

date_API = []

date = start_date
while date <= end_date:
    date_API.append(date.strftime('%Y-%m-%d'))
    date = date + relativedelta(months=1)

date_API

['2019-01-01',
 '2019-02-01',
 '2019-03-01',
 '2019-04-01',
 '2019-05-01',
 '2019-06-01',
 '2019-07-01',
 '2019-08-01',
 '2019-09-01',
 '2019-10-01',
 '2019-11-01',
 '2019-12-01',
 '2020-01-01',
 '2020-02-01',
 '2020-03-01']

In [ ]:
weather = []

for d in date_API:
    time.sleep(2)
    response = requests.get(f'https://api-datalab.coderslab.com/api/v2/airportWeather?date={d}', headers={'Authorization': f'{authorization}'})
    if response.status_code == 200:
        weather.append(response.json())
    else:
        pass

weather

[[{'WT18': None,
   'STATION': 'USW00013874',
   'NAME': 'ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US',
   'DATE': '2019-01-01',
   'AWND': 4.7,
   'PRCP': 0.14,
   'SNOW': 0,
   'SNWD': 0,
   'TAVG': 64,
   'TMAX': 66,
   'TMIN': 57,
   'WDF2': 310,
   'WDF5': 310,
   'WSF2': 15,
   'WSF5': 19,
   'WT01': 1},
  {'WT18': None,
   'STATION': 'USW00013874',
   'NAME': 'ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US',
   'DATE': '2019-01-02',
   'AWND': 4.92,
   'PRCP': 0.57,
   'SNOW': 0,
   'SNWD': 0,
   'TAVG': 56,
   'TMAX': 59,
   'TMIN': 49,
   'WDF2': 70,
   'WDF5': 50,
   'WSF2': 12.1,
   'WSF5': 15,
   'WT01': 1,
   'WT08': 1},
  {'WT18': None,
   'STATION': 'USW00013874',
   'NAME': 'ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US',
   'DATE': '2019-01-03',
   'AWND': 5.37,
   'PRCP': 0.15,
   'SNOW': 0,
   'SNWD': 0,
   'TAVG': 52,
   'TMAX': 55,
   'TMIN': 51,
   'WDF2': 340,
   'WDF5': 330,
   'WSF2': 15,
   'WSF5': 18.1,
   'WT01': 1},
  {'WT18':

In [ ]:
airport_weather = []

for i in range(0,15):
    df = pd.DataFrame.from_records(weather[i])
    airport_weather.append(df)
airport_weather

[      WT18      STATION                                               NAME  \
 0     None  USW00013874  ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPO...   
 1     None  USW00013874  ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPO...   
 2     None  USW00013874  ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPO...   
 3     None  USW00013874  ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPO...   
 4     None  USW00013874  ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPO...   
 ...    ...          ...                                                ...   
 3281  None  USW00093805                TALLAHASSEE REGIONAL AIRPORT, FL US   
 3282  None  USW00093805                TALLAHASSEE REGIONAL AIRPORT, FL US   
 3283  None  USW00093805                TALLAHASSEE REGIONAL AIRPORT, FL US   
 3284  None  USW00093805                TALLAHASSEE REGIONAL AIRPORT, FL US   
 3285  None  USW00093805                TALLAHASSEE REGIONAL AIRPORT, FL US   
 
             DATE   AWND  PRCP  SNOW  SNWD  TAVG  

In [ ]:
airport_weather_df = pd.concat(airport_weather)
airport_weather_df

WT18      STATION                                               NAME  \
0     None  USW00013874  ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPO...   
1     None  USW00013874  ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPO...   
2     None  USW00013874  ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPO...   
3     None  USW00013874  ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPO...   
4     None  USW00013874  ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPO...   
...    ...          ...                                                ...   
2568  None  USW00014762             PITTSBURGH ALLEGHENY CO AIRPORT, PA US   
2569  None  USW00014762             PITTSBURGH ALLEGHENY CO AIRPORT, PA US   
2570  None  USW00014762             PITTSBURGH ALLEGHENY CO AIRPORT, PA US   
2571  None  USW00014762             PITTSBURGH ALLEGHENY CO AIRPORT, PA US   
2572  None  USW00014762             PITTSBURGH ALLEGHENY CO AIRPORT, PA US   

            DATE   AWND  PRCP  SNOW  SNWD  TAVG  TMAX  ...    PGTM  WT10  \
0     2019-01-01   4.70  0.14   0.0   0.0  64.0  66.0  ...     NaN   NaN   
1     2019-01-02   4.92  0.57   0.0   0.0  56.0  59.0  ...     NaN   NaN   
2     2019-01-03   5.37  0.15   0.0   0.0  52.0  55.0  ...     NaN   NaN   
3     2019-01-04  12.08  1.44   0.0   0.0  56.0  66.0  ...     NaN   NaN   
4     2019-01-05  13.42  0.00   0.0   0.0  49.0  59.0  ...     NaN   NaN   
...          ...    ...   ...   ...   ...   ...   ...  ...     ...   ...   
2568  2020-03-27   3.58  0.21   NaN   NaN   NaN  59.0  ...   146.0   NaN   
2569  2020-03-28   6.93  1.29   NaN   NaN   NaN  77.0  ...  1535.0   NaN   
2570  2020-03-29  16.55  0.02   NaN   NaN   NaN  78.0  ...  1408.0   NaN   
2571  2020-03-30  13.42  0.00   NaN   NaN   NaN  57.0  ...   817.0   NaN   
2572  2020-03-31   3.80  0.06   NaN   NaN   NaN  47.0  ...   110.0   NaN   

      WESD  SN32  SX32  PSUN  TSUN  TOBS  WT07  WT11  
0      NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  
1      NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  
2      NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  
3      NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  
4      NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  
...    ...   ...   ...   ...   ...   ...   ...   ...  
2568   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  
2569   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  
2570   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  
2571   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  
2572   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  

[46226 rows x 33 columns]

 ## Sprawdzenie
 Uruchom kod poniżej, aby sprawdzić, czy ta część została poprawnie wykonana

In [ ]:
airport_weather_df_expected_shape = (46226, 33)
assert airport_weather_df_expected_shape == airport_weather_df.shape

 ## Zapis do pliku
 Tutaj zapisz ramkę `weather_df` do pliku `airport_weather.csv` w katalogu `data/raw`

In [ ]:
airport_weather_df.to_csv(r'C:\Users\urszu\OneDrive\Pulpit\CodersLab - cwiczenia\Projekt koncowy\data\raw\airport_weather.csv', index=False)

 # Pobranie `Aircraft`
 Zapoznaj się z dokumentacją endpointu `aircraft`, a następnie pobierz dane produkcyjne samolotów. Wyniki zapisz do ramki `aircraft_df`, a następnie zapisz do pliku `aircraft.csv`.


In [ ]:
response = requests.get('https://api-datalab.coderslab.com/api/v2/aircraft', headers={'Authorization': f'{authorization}'})
aircraft = response.json()
aircraft

[{'MANUFACTURE_YEAR': 1944, 'TAIL_NUM': 'N54514', 'NUMBER_OF_SEATS': 0},
 {'MANUFACTURE_YEAR': 1945, 'TAIL_NUM': 'N1651M', 'NUMBER_OF_SEATS': 0},
 {'MANUFACTURE_YEAR': 1953, 'TAIL_NUM': 'N100CE', 'NUMBER_OF_SEATS': 0},
 {'MANUFACTURE_YEAR': 1953, 'TAIL_NUM': 'N141FL', 'NUMBER_OF_SEATS': 0},
 {'MANUFACTURE_YEAR': 1953, 'TAIL_NUM': 'N151FL', 'NUMBER_OF_SEATS': 0},
 {'MANUFACTURE_YEAR': 1953, 'TAIL_NUM': 'N381FL', 'NUMBER_OF_SEATS': 0},
 {'MANUFACTURE_YEAR': 1954, 'TAIL_NUM': 'N6174C', 'NUMBER_OF_SEATS': 0},
 {'MANUFACTURE_YEAR': 1954, 'TAIL_NUM': 'N400UA', 'NUMBER_OF_SEATS': 0},
 {'MANUFACTURE_YEAR': 1955, 'TAIL_NUM': 'N747CE', 'NUMBER_OF_SEATS': 2},
 {'MANUFACTURE_YEAR': 1955, 'TAIL_NUM': 'N9148F', 'NUMBER_OF_SEATS': 0},
 {'MANUFACTURE_YEAR': 1955, 'TAIL_NUM': 'N131FL', 'NUMBER_OF_SEATS': 0},
 {'MANUFACTURE_YEAR': 1955, 'TAIL_NUM': 'N351FL', 'NUMBER_OF_SEATS': 0},
 {'MANUFACTURE_YEAR': 1955, 'TAIL_NUM': 'N391FL', 'NUMBER_OF_SEATS': 0},
 {'MANUFACTURE_YEAR': 1956, 'TAIL_NUM': 'N171FL', '

In [ ]:
aircraft_df = pd.DataFrame.from_records(aircraft)
aircraft_df

MANUFACTURE_YEAR TAIL_NUM  NUMBER_OF_SEATS
0                 1944   N54514              0.0
1                 1945   N1651M              0.0
2                 1953   N100CE              0.0
3                 1953   N141FL              0.0
4                 1953   N151FL              0.0
...                ...      ...              ...
7378              2019   N14011            337.0
7379              2019   N16008            337.0
7380              2019   N16009            337.0
7381              2019   N2250U            276.0
7382              2019   N2749U            276.0

[7383 rows x 3 columns]

 ## Sprawdzenie
 Uruchom kod poniżej, aby sprawdzić, czy ta część została poprawnie wykonana

In [ ]:
aircraft_df_expected_shape = (7383, 3)
assert aircraft_df_expected_shape == aircraft_df.shape

 ## Zapis do pliku
 Tutaj zapisz ramkę `aircraft_df` do pliku `aircraft.csv` w katalogu `data/raw`

In [ ]:
aircraft_df.to_csv(r'C:\Users\urszu\OneDrive\Pulpit\CodersLab - cwiczenia\Projekt koncowy\data\raw\aircraft.csv', index=False)

 # Pobranie `Flight`
 Zapoznaj się z dokumentacją endpointu `flights`, następnie pobierz dane dotyczące ruchu lotniczego. Wyniki zapisz do ramki `flight_df`, a później do pliku `flight.csv`.

 Wskazówki:
 - Zwróć szczególną uwagę na konstrukcję endpointa,
 - Ze względu na wolumen danych, które tutaj się pobiorą, odradzamy zapisywanie danych bezpośrednio do ramki. Rekomendujemy podejście podobne do tego, z warsztatu na kursie `Python - analiza danych` - `Dzień 10 - Warsztat > Warsztat > Scrapowanie danych`,
 - Data początkowa danych to `2019-01-01`, zaś końcowa to `2020-03-31`, czyli 456 dni,
 - Ze względu na czas, jaki ten krok będzie się wykonywał, warto dodać w pętli instrukcję (lub kilka) `print`, aby monitorować przebieg wykonywania tego kroku,
 - W przypadku, gdy nie ma dostępnych danych dla danego lotniska, API zwraca kod [204](https://developer.mozilla.org/en-US/docs/Web/HTTP/Status/204), w ten sposób możesz pominąć lotniska, dla których dane nie są dostępne,
 - Pobranie całości danych zajmuje dłuższą chwilę, zanim włączysz pętle dla wszystkich danych, sprawdź pobieranie danych dla jednego, dwóch lotnisk aby uniknąć frustracji.

In [18]:
airportId

[10874,
 11233,
 13360,
 15008,
 11638,
 14150,
 15323,
 14814,
 12007,
 11337,
 13342,
 15070,
 13244,
 12280,
 15096,
 11641,
 13832,
 10268,
 10397,
 15041,
 10529,
 12119,
 11537,
 11092,
 10581,
 13829,
 15389,
 10140,
 12389,
 11648,
 15023,
 11982,
 10967,
 11525,
 10792,
 14259,
 11637,
 10466,
 10599,
 10208,
 15841,
 14831,
 12898,
 13241,
 13367,
 11481,
 14108,
 13931,
 13873,
 10157,
 10245,
 11146,
 13277,
 11292,
 11109,
 13459,
 11775,
 16218,
 14698,
 14252,
 13256,
 13139,
 12250,
 11259,
 11468,
 14952,
 12402,
 14574,
 11996,
 11977,
 11867,
 11203,
 11995,
 15016,
 10747,
 14905,
 12012,
 14783,
 14730,
 10431,
 10434,
 16869,
 10408,
 12264,
 11618,
 15304,
 13577,
 12954,
 11624,
 13541,
 13422,
 14057,
 13232,
 10800,
 14689,
 12391,
 10868,
 14711,
 10257,
 11067,
 10562,
 11695,
 13796,
 14109,
 13970,
 14193,
 11076,
 14092,
 11122,
 11288,
 11308,
 10754,
 12884,
 15376,
 14588,
 11884,
 12915,
 13851,
 14843,
 11603,
 14457,
 12206,
 11252,
 11905,
 15412,


In [19]:
date_API

['2019-01-01',
 '2019-02-01',
 '2019-03-01',
 '2019-04-01',
 '2019-05-01',
 '2019-06-01',
 '2019-07-01',
 '2019-08-01',
 '2019-09-01',
 '2019-10-01',
 '2019-11-01',
 '2019-12-01',
 '2020-01-01',
 '2020-02-01',
 '2020-03-01']

In [10]:
response = requests.get(f'https://api-datalab.coderslab.com/api/v2/flight?airportId=10397&date=2019-01-01', headers={'Authorization': f'{authorization}'})
flight = response.json()
flight

[{'MONTH': 1,
  'DAY_OF_MONTH': 20,
  'DAY_OF_WEEK': 7,
  'OP_UNIQUE_CARRIER': 'WN',
  'TAIL_NUM': 'N204WN',
  'OP_CARRIER_FL_NUM': 682,
  'ORIGIN_AIRPORT_ID': 10397,
  'DEST_AIRPORT_ID': 11292,
  'CRS_DEP_TIME': 605,
  'DEP_TIME': 602,
  'DEP_DELAY_NEW': 0,
  'DEP_TIME_BLK': '0600-0659',
  'CRS_ARR_TIME': 730,
  'ARR_TIME': 726,
  'ARR_DELAY_NEW': 0,
  'ARR_TIME_BLK': '0700-0759',
  'CANCELLED': 0,
  'CRS_ELAPSED_TIME': 205,
  'ACTUAL_ELAPSED_TIME': 204,
  'DISTANCE': 1199,
  'DISTANCE_GROUP': 5,
  'YEAR': 2019},
 {'MONTH': 1,
  'DAY_OF_MONTH': 20,
  'DAY_OF_WEEK': 7,
  'OP_UNIQUE_CARRIER': 'WN',
  'TAIL_NUM': 'N8682B',
  'OP_CARRIER_FL_NUM': 2622,
  'ORIGIN_AIRPORT_ID': 10397,
  'DEST_AIRPORT_ID': 11292,
  'CRS_DEP_TIME': 2120,
  'DEP_TIME': 2114,
  'DEP_DELAY_NEW': 0,
  'DEP_TIME_BLK': '2100-2159',
  'CRS_ARR_TIME': 2250,
  'ARR_TIME': 2239,
  'ARR_DELAY_NEW': 0,
  'ARR_TIME_BLK': '2200-2259',
  'CANCELLED': 0,
  'CRS_ELAPSED_TIME': 210,
  'ACTUAL_ELAPSED_TIME': 205,
  'DISTANCE': 1

In [ ]:
flights = []

for d in date_API:
    for i in airportId:
        time.sleep(2)
        response = requests.get(f'https://api-datalab.coderslab.com/api/v2/flight?airportId={i}&date={d}', headers={'Authorization': f'{authorization}'})
        if response.status_code == 200:
            flights.append(response.json())
        else:
            pass

flights

In [ ]:
flight_list = []

for i in range(0,15):
    df = pd.DataFrame.from_records(flights[i])
    flight_list.append(df)
flight_list

In [ ]:
flight_df = pd.concat(flight_list)
flight_df

 ## Sprawdzenie
 Uruchom kod poniżej, aby sprawdzić, czy ta część została poprawnie wykonana

In [ ]:
flight_df_expected_shape = (1386120, 27)
assert flight_df_expected_shape == flight_df.shape

 ## Zapis do pliku
 Tutaj zapisz ramkę `flight_df` do pliku `flight.csv` w katalogu `data/raw`

In [ ]:
flight1_df.to_csv(r'C:\Users\urszu\OneDrive\Pulpit\CodersLab - cwiczenia\Projekt koncowy\data\raw\flight.csv', index=False)

 # Podsumowanie
 W tym notatniku wykonaliśmy podstawowy krok w analizie danych - pozyskaliśmy je. Są gotowe do dalszej pracy, czyli możemy załadować je na bazę danych, a następnie zapoznać się z tym, jakie informacje ze sobą niosą. Kolejne notatniki będą służyły właśnie tym celom.

In [1]:
msg = "Wszystko wygląda OK :) Możesz przejść do kolejnego kroku."
print(msg)

Wszystko wygląda OK :) Możesz przejść do kolejnego kroku.
